In [2]:
"""
Multi-Agent Dynamic Grid World Environment
Created by: Ardianto Wibowo
"""

import numpy as np
import sys
import random

# Add the path to the 'env' folder to sys.path
sys.path.append('env')

from ma_gridworld import Env

class SearchAgent:
    def __init__(self, num_actions, env):
        self.num_actions = num_actions
        self.targets_seen = []
        self.memory = []
        self.env = env  # مرجع البيئة
        self.agent_trust_levels = env.agent_trust_levels  # استدعاء مستويات الثقة من البيئة
        
        
        




    def analyse_sensor_data(self, agent_id, coordinate_observation, sensor_data_observation):
        for i in range(len(sensor_data_observation)):
            for j in range(len(sensor_data_observation[i])):
                data = sensor_data_observation[i][j]
                location = [coordinate_observation[0] + j - len(sensor_data_observation[i])//2,
                           coordinate_observation[1] + i - len(sensor_data_observation)//2]
                if data != None and 'target_' + str(agent_id) in data:
                    if location not in self.targets_seen:
                        self.targets_seen.append(location)
                    # تحديث الذاكرة مع تمرير agent_id
                if data is not None and 'target_' in data:  # التحقق من وجود هدف
                    self.update_memory(location, data, agent_id)  # استدعاء update_memory

                # تطبيق الضوضاء بناءً على معدل الخطأ الخاص بالوكيل
                error_rate = 1 - self.agent_trust_levels[agent_id]  # معدل الخطأ للوكيل نفسه
                if is_noise_enabled:  # إذا كانت الضوضاء مفعلة
                    location = [
                        location[0] + int(error_rate * random.choice([-1, 0, 1])),
                        location[1] + int(error_rate * random.choice([-1, 0, 1]))
                    ]
                    print(f"Agent {agent_id}: Noise applied to sensor data. Original: {coordinate_observation}, Noisy: {location}")

                # إزالة الأهداف التي تم جمعها
                if location[0] == coordinate_observation[0] and location[1] == coordinate_observation[1]:
                    if location in self.targets_seen:
                        self.targets_seen.remove(location)








        
    def analyse_communication(self, comm_observation, agent_id):
            for comm in comm_observation:
                origin_location = comm[0]
                sensor_data_observation = comm[1]
                reported_by = comm[2]

                print(f"Agent {agent_id}: Received communication from Agent {reported_by} at {origin_location}")

                for i in range(len(sensor_data_observation)):
                    for j in range(len(sensor_data_observation[i])):
                        data = sensor_data_observation[i][j]
                        location = [origin_location[0] + j - len(sensor_data_observation[i]) // 2,
                                    origin_location[1] + i - len(sensor_data_observation) // 2]

                        # تطبيق الضوضاء بناءً على معدل الخطأ الخاص بالوكيل المرسل
                        error_rate = 1 - self.agent_trust_levels[reported_by]  # معدل الخطأ للوكيل المرسل
                        if is_noise_enabled:  # إذا كانت الضوضاء مفعلة
                            location = [
                                location[0] + int(error_rate * random.choice([-1, 0, 1])),
                                location[1] + int(error_rate * random.choice([-1, 0, 1]))
                            ]
                            print(f"Agent {agent_id}: Noise applied to communication. Original: {origin_location}, Noisy: {location}")

                        if data is not None and 'target_' + str(agent_id) in data:
                            if location not in self.targets_seen:
                                self.targets_seen.append(location)
                                print(f"Agent {agent_id}: Added noisy target at {location} from Agent {reported_by}")                  
                           
                            
    def update_memory(self, location, data, agent_id):

        print(f"Agent {agent_id} is updating memory for location {location} with data {data}")
        if location not in [record["location"] for record in self.memory]:
            # add
            self.memory.append({"location": location, "data": data})
            print(f"Agent {agent_id} Updated Memory: {location} -> {data}")





    def select_action(self, coordinate_observation, agent_id):
        print(f"Agent {agent_id}: Current targets seen: {self.targets_seen}")
        if len(self.targets_seen) > 0:
            closest_target = None
            closest_target_distance = 999999
            for target_coordinate in self.targets_seen:
                horizontal_distance = target_coordinate[0] - coordinate_observation[0]
                vertical_distance = target_coordinate[1] - coordinate_observation[1]
                distance = abs(horizontal_distance) + abs(vertical_distance)
                if distance < closest_target_distance:
                    closest_target_distance = distance
                    closest_target = target_coordinate

            if closest_target:
                print(f"Agent {agent_id}: Moving towards target at {closest_target}")
                horizontal_distance = closest_target[0] - coordinate_observation[0]
                vertical_distance = closest_target[1] - coordinate_observation[1]
                if abs(horizontal_distance) >= abs(vertical_distance):
                    return 3 if horizontal_distance < 0 else 4
                else:
                    return 1 if vertical_distance < 0 else 2
        else:
            print(f"Agent {agent_id}: No targets seen, taking random action.")
            return np.random.choice(self.num_actions - 1) + 1





def get_action(agent_id, observation, num_actions, agents, env):
    """
    This method provides a random action chosen recognized by the ma-gridworld environment:
    1: up, 2: down, 3: left, 4: right, 0: stay
    """
    
    coordinate_observation = tuple(observation[0])  # Keep observation as (x, y) tuple

    # Optional observation data may be used, depend on the agent needs.
    win_state_observation = observation[1]
    sensor_data_observation = observation[2]
    comm_observation = observation[3]
    

    print(f"Observation for Agent {agent_id}: {observation}")

    # Check if communication data is available
    if comm_observation:
        agents[agent_id].analyse_communication(comm_observation, agent_id)
    else:
        print(f"Agent {agent_id}: No communication data available this step.")

    # Analyze sensor data
    agents[agent_id].analyse_sensor_data(agent_id, coordinate_observation, sensor_data_observation)
    
    # Select physical action
    physical_action = agents[agent_id].select_action(coordinate_observation, agent_id)

    # Define communication action
    if env.is_agent_silent:
        comm_action = []  # Communication action is set to be zero if agent silent
    else:
        comm_action = [coordinate_observation, sensor_data_observation, agent_id] 
    
    return (physical_action, comm_action)


def run(num_episodes, max_steps_per_episode, agents, num_actions, env):
    agent_steps = []
    for episode in range(num_episodes):
        print(f"Starting episode {episode + 1}")
        
        # طباعة درجات الثقة ومعدلات الخطأ
        print("Agent Trust Levels and Error Rates:")
        for i, trust_level in enumerate(env.agent_trust_levels):
            error_rate = round(1 - trust_level, 2)
            print(f"  Agent {i}: Trust Level = {trust_level}, Error Rate = {error_rate}")

        observations = env.reset()  # Reset the environment at the start of each episode
        
        for agent in agents:
            agent.targets_seen = []
            agent.memory = []

        
        done = [False] * env.num_agents  # Initialize 'done' as a list for each agent
        step_count = 0

        while not all(done) and step_count < max_steps_per_episode:  # Stop if all agents are done or max steps reached
            actions = []
            next_observations = []
            
            for agent_id in range(env.num_agents):
                observation = observations[agent_id]
                action = get_action(agent_id, observation, num_actions, agents, env)
                
                actions.append(action)
                next_observations.append(observation)

            next_observations, rewards, done = env.step(actions)  # Step in the environment

            observations = next_observations
            step_count += 1

            # Render the environment
            env.render()

            # طباعة النتائج على الشاشة
            print(f"Step {step_count}:")
            for agent_id in range(env.num_agents):
                print(
                    f"  Agent {agent_id}: Observation: {observations[agent_id]}, "
                    f"Action: {actions[agent_id]}, Reward: {rewards[agent_id]}, Done: {done[agent_id]}"
                )

        # طباعة عدد الخطوات عند نهاية الحلقة
        print(f"Episode {episode + 1} finished after {step_count} steps.\n")





if __name__ == "__main__":

    gsize=15 #grid size (square)
    gpixels=30 #grid cell size in pixels

    is_sensor_active = True #True:  Activate the sensory observation data
    sensory_size = 3 #'is_sensor_active' must be True. The value must be odd, if event will be converted to one level odd number above
    
    num_agents = 10 #the number of agents will be run in paralel
    num_obstacles = 0 #the number of obstacles
    is_single_target = False #True: all agents have a single target, False: each agent has their own target
    num_targets_per_agent = 5 #'is_single_target' must be true to have an effect
    
    is_agent_silent = False #True: communication among agents is allowed
    
    
    is_noise_enabled = True  # تفعيل الضوضاء
    location_noise_probability = 0.8

    num_episodes=1 #the number of episode will be run
    max_steps_per_episode=1000 #each episode will be stopped when max_step is reached

    eps_moving_targets = 10 #set this value greater than 'num_episodes' to keep the targets in a stationary position
    eps_moving_obstacles = 10 #set this value greater than 'num_episodes' to keep the obstacles in a stationary position

    render = True #True: render the animation into the screen (so far, it is still can not be deactivated)

    min_obstacle_distance_from_target = 1 #min grid distance of each obstacles relative to targets
    max_obstacle_distance_from_target = 5 #max grid distance of each obstacles relative to targets
    min_obstacle_distance_from_agents = 1 #min grid distance of each obstacles relative to agents

    reward_normal = -1 #reward value of normal steps
    reward_obstacle = -5 #reward value when hit an obstacle
    reward_target = 50 #reward value when reach the target

    is_totally_random = True #True: target and obstacles initial as well as movement position is always random on each call, False: only random at the beginning. 
    animation_speed = 0.1 #smaller is faster 
    is_destroy_environment = True #True: automatically close the animation after all episodes end.  

    # Initialize environment
    env = Env(
        num_agents=num_agents, num_targets_per_agent=num_targets_per_agent, num_obstacles=num_obstacles,
        eps_moving_obstacles=eps_moving_obstacles, eps_moving_targets=eps_moving_targets,
        is_agent_silent=is_agent_silent, is_single_target=is_single_target, sensory_size=sensory_size,
        gpixels=gpixels, gheight=gsize, gwidth=gsize, is_sensor_active=is_sensor_active,
        min_obstacle_distance_from_target=min_obstacle_distance_from_target,
        max_obstacle_distance_from_target=max_obstacle_distance_from_target,
        min_obstacle_distance_from_agents=min_obstacle_distance_from_agents,
        is_totally_random=is_totally_random, animation_speed=animation_speed,
        reward_normal=reward_normal, reward_obstacle=reward_obstacle, reward_target=reward_target
    )
    
    num_actions = len(env.action_space)
    
    # Initialize Q-learning agents
    agents = [SearchAgent(num_actions, env) for _ in range(num_agents)]

    # Run episodes
    run(num_episodes, max_steps_per_episode, agents, num_actions, env)

    if is_destroy_environment:
        env.destroy_environment() 


Starting episode 1
Agent Trust Levels and Error Rates:
  Agent 0: Trust Level = 0.8, Error Rate = 0.2
  Agent 1: Trust Level = 0.19, Error Rate = 0.81
  Agent 2: Trust Level = 0.49, Error Rate = 0.51
  Agent 3: Trust Level = 0.32, Error Rate = 0.68
  Agent 4: Trust Level = 0.67, Error Rate = 0.33
  Agent 5: Trust Level = 0.66, Error Rate = 0.34
  Agent 6: Trust Level = 0.34, Error Rate = 0.66
  Agent 7: Trust Level = 0.98, Error Rate = 0.02
  Agent 8: Trust Level = 0.42, Error Rate = 0.58
  Agent 9: Trust Level = 0.36, Error Rate = 0.64
Episode 1: Trust Levels and Error Rates
  Agent 0: Trust Level = 0.8, Error Rate = 0.2
  Agent 1: Trust Level = 0.19, Error Rate = 0.81
  Agent 2: Trust Level = 0.49, Error Rate = 0.51
  Agent 3: Trust Level = 0.32, Error Rate = 0.68
  Agent 4: Trust Level = 0.67, Error Rate = 0.33
  Agent 5: Trust Level = 0.66, Error Rate = 0.34
  Agent 6: Trust Level = 0.34, Error Rate = 0.66
  Agent 7: Trust Level = 0.98, Error Rate = 0.02
  Agent 8: Trust Level = 0.

Step 2:
  Agent 0: Observation: [[1, 1], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'target_5_2'], ['empty', 'empty', 'empty']], [[(14, 1), [['empty', 'agent', None], ['target_8_1', 'empty', None], ['empty', 'empty', None]], 1], [(14, 14), [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(0, 14), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, None, None]], 3], [(4, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 4], [(8, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'target_1_0', 'empty']], 5], [(13, 5), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 6], [(13, 9), [['empty', 'empty', 'empty'], ['target_0_2', 'empty', 'agent'], ['target_1_1', 'empty', 'empty']], 7], [(7, 13), [['target_4_0', 'target_0_1', 'empty'], ['empty', 'empty', 'target_9_1'], ['empty', 'agent', 'empty']], 8], [(1, 7), [['empty', 'target_9_3', 'target_5_1'], ['agent

Step 4:
  Agent 0: Observation: [[1, 3], False, [['empty', 'agent', 'empty'], ['empty', 'target_3_0', 'target_1_2'], ['empty', 'target_6_1', 'target_7_2']], [[(12, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['target_6_0', 'target_9_3', 'empty']], 1], [(14, 13), [['empty', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 2], [(0, 13), [[None, 'empty', 'empty'], [None, 'empty', 'empty'], [None, 'agent', 'empty']], 3], [(4, 2), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['target_5_3', 'empty', 'empty']], 4], [(7, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 5], [(13, 5), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(14, 8), [['target_1_4', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 7], [(7, 11), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['target_4_0', 'agent', 'empty']], 8], [(2, 6), [['empty', '

Step 6:
  Agent 0: Observation: [[1, 5], False, [['empty', 'agent', 'target_7_2'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'target_5_1']], [[(10, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'target_6_0']], 1], [(13, 14), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], [None, None, None]], 2], [(0, 11), [[None, 'empty', 'empty'], [None, 'empty', 'empty'], [None, 'agent', 'empty']], 3], [(4, 4), [['target_5_3', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(5, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 5], [(12, 4), [['empty', 'target_3_3', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 6], [(14, 7), [['empty', 'empty', None], ['target_1_4', 'empty', None], ['empty', 'agent', None]], 7], [(8, 10), [['empty', 'target_3_4', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 8], [(3, 7), [['target_5_1', 'empty

Step 8:
  Agent 0: Observation: [[2, 6], False, [['empty', 'empty', 'empty'], ['agent', 'target_5_1', 'empty'], ['empty', 'empty', 'empty']], [[(8, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 1], [(12, 13), [['empty', 'empty', 'empty'], ['target_5_4', 'empty', 'agent'], ['empty', 'empty', 'empty']], 2], [(1, 10), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 3], [(4, 6), [['empty', 'agent', 'empty'], ['empty', 'target_6_3', 'target_2_4'], ['empty', 'empty', 'target_8_0']], 4], [(3, 1), [['empty', 'empty', 'empty'], ['target_5_2', 'empty', 'agent'], ['empty', 'empty', 'empty']], 5], [(11, 3), [['empty', 'target_6_0', 'target_9_3'], ['target_2_2', 'empty', 'agent'], ['empty', 'empty', 'empty']], 6], [(12, 7), [['target_8_2', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 7], [(8, 8), [['empty', 'target_0_0', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', '

...

Step 54:
  Agent 0: Observation: [[4, 13], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], [[(8, 10), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 1], [(14, 1), [['empty', 'agent', None], ['empty', 'empty', None], ['empty', 'empty', None]], 2], [(4, 9), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'agent']], 3], [(6, 8), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(8, 11), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 5], [(7, 1), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(14, 11), [['empty', 'empty', None], ['agent', 'empty', None], ['empty', 'empty', None]], 7], [(6, 10), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 8], [(4, 14), [['empty', 'agent', 'empty'], ['empty', 'agent

Step 56:
  Agent 0: Observation: [[6, 13], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['agent', 'empty', 'empty']], [[(9, 11), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 1], [(14, 1), [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None]], 2], [(4, 7), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'agent']], 3], [(5, 9), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(6, 11), [['empty', 'empty', 'empty'], ['empty', 'agent', 'agent'], ['empty', 'empty', 'empty']], 5], [(6, 0), [[None, None, None], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 6], [(14, 10), [['empty', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 7], [(6, 10), [['agent', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 8], [(5, 14), [['empty', 'agent', 'empty'], ['agent', 'empty', 'empty

Step 58:
  Agent 0: Observation: [[6, 13], False, [['agent', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], [[(8, 12), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 1], [(14, 1), [['empty', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 2], [(5, 8), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['agent', 'empty', 'empty']], 3], [(4, 10), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(6, 9), [['agent', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'agent']], 5], [(5, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 6], [(14, 10), [['empty', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 7], [(8, 10), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 8], [(5, 12), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty

Step 60:
  Agent 0: Observation: [[7, 12], False, [['empty', 'agent', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], [[(7, 11), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['agent', 'agent', 'empty']], 1], [(13, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 2], [(5, 8), [['empty', 'agent', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 3], [(3, 11), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['target_4_0', 'empty', 'empty']], 4], [(5, 8), [['empty', 'empty', 'empty'], ['empty', 'agent', 'agent'], ['empty', 'empty', 'empty']], 5], [(6, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(13, 9), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 7], [(6, 10), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['agent', 'empty', 'agent']], 8], [(5, 10), [['empty', 'empty', 'empty'], ['empty', 'e

Step 62:
  Agent 0: Observation: [[6, 13], True, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], [[(7, 9), [['agent', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 1], [(13, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 2], [(6, 9), [['empty', 'agent', 'empty'], ['agent', 'empty', 'agent'], ['empty', 'empty', 'empty']], 3], [(2, 12), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(6, 9), [['empty', 'agent', 'empty'], ['empty', 'agent', 'agent'], ['empty', 'empty', 'empty']], 5], [(7, 1), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(11, 9), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 7], [(6, 12), [['agent', 'agent', 'empty'], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 8], [(6, 11), [['empty', 'empty', 'empty'], ['agent', 